In [2]:
from bokeh.plotting import figure
from bokeh.io import show, output_notebook
from bokeh.layouts import column, row
from bokeh.models import Range1d
output_notebook()

import numpy as np

from voltagebudget import util
from voltagebudget import neurons
from voltagebudget.util import locate_firsts
from voltagebudget.util import locate_peaks
from voltagebudget.util import filter_voltages
from fakespikes import util as fsutil

Loading BokehJS ...

/Users/type/anaconda/envs/py2/lib/python2.7/site-packages/brian2/core/variables.py:174: FutureWarning: Conversion of the second argument of issubdtype from `float` to `np.floating` is deprecated. In future, it will be treated as `np.float64 == np.dtype(float).type`.
  return np.issubdtype(np.bool, self.dtype)


In [10]:
t = 0.4
stim_number = 10
stim_onset = 0.2
stim_offset = 0.25
stim_rate = 20
dt = 1e-5
seed_stim = 7525
ns_x, ts_x = util.poisson_impulse(
        t,
        stim_onset,
        stim_offset - stim_onset,
        stim_rate,
        n=stim_number,
        dt=dt,
        seed=seed_stim)

In [11]:
print(">>> {} spikes".format(ts_x.size))
print(">>> ts_x min {}, max {}".format(ts_x.min(), ts_x.max()))
print(">>> {} population rate".format(ts_x.size / (stim_offset - stim_onset)))
print(">>> {} single unit rate".format((ts_x.size / float(stim_number)) / (stim_offset - stim_onset)))

>>> 8 spikes
>>> ts_x min 0.20771519288, max 0.242806070152
>>> 160.0 population rate
>>> 16.0 single unit rate


In [12]:
p = figure(plot_width=400, plot_height=200)
p.circle(ts_x, ns_x, color="black")
p.xaxis.axis_label = 'Time (s)'
p.yaxis.axis_label = 'N'
p.x_range = Range1d(0, t)
p.xgrid.grid_line_color = None
p.ygrid.grid_line_color = None
show(p)

In [26]:
mode = 'regular'

params, w_in, bias_in, _ = util.read_modes(mode)
N = 50

k1 = 3
k2 = 3
w_in = [w_in[0] * k1, w_in[1] * k2]

ns_y, ts_y, budget_y = neurons.adex(N, t, 
                                    ns_x, ts_x, 
                                    w_in=w_in, 
                                    bias_in=bias_in, 
                                    sigma=0, 
                                    A=0, f=0, phi=0, 
                                    **params)

In [27]:
print(">>> {} spikes".format(ts_y.size))
print(">>> ts_y min {}, max {}".format(ts_y.min(), ts_y.max()))
print(">>> {} population rate".format(ts_y.size / (stim_offset - stim_onset)))
print(">>> {} single unit rate".format((ts_y.size / float(N)) / (stim_offset - stim_onset)))

>>> 123 spikes
>>> ts_y min 0.22133, max 0.2561
>>> 2460.0 population rate
>>> 49.2 single unit rate


In [28]:
p = figure(plot_width=400, plot_height=200)
p.circle(ts_y, ns_y, color="black")
p.xaxis.axis_label = 'Time (s)'
p.yaxis.axis_label = 'N'
p.x_range = Range1d(0, t)
p.xgrid.grid_line_color = None
p.ygrid.grid_line_color = None
show(p)

In [29]:
times = budget_y['times']

p = figure(plot_width=400, plot_height=200)
for n in range(10):
    v = budget_y['V_m'][n, :]
    p.line(x=times, y=v, color="black", alpha=0.1)
p.xaxis.axis_label = 'Time (s)'
p.yaxis.axis_label = 'Vm (volts)'
p.xgrid.grid_line_color = None
p.ygrid.grid_line_color = None
show(p)